In [0]:
from pyspark.sql.functions import *
from pyspark.sql.types import *

In [0]:
init_load_flag = int(dbutils.widgets.get("init_load_flag"))

### **Data Reading From Source**

In [0]:
df = spark.sql("select * from databricks_cata.silver.customers_silver")

### **Remove Duplicates**

In [0]:
df = df.dropDuplicates(subset=['customer_id'])

In [0]:
df.limit(10).display()

customer_id email city state domains full_name C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green C00010 charles58@murillo.net West Hector OK murillo.net James Myers

## ### **Dividing New Vs Old Records**

In [0]:
if init_load_flag == 0:
    df_old=spark.sql('''select DimCustomerKey, customer_id, create_date, update_date from databricks_cata.gold.DimCustomers''')

else:
    df_old=spark.sql('''select 0 DimCustomerKey, 0 customer_id, 0 create_date, 0 update_date from databricks_cata.silver.customers_silver where 1=0''')


In [0]:
df_old.display()

DimCustomerKey customer_id create_date update_date

### **Renaming Columns of df_old**

In [0]:
df_old = df_old.withColumnRenamed("DimCustomerKey", "old_DimCustomerKey")\
  .withColumnRenamed("customer_id", "old_customer_id")\
  .withColumnRenamed("create_date", "old_create_date")\
  .withColumnRenamed("update_date", "old_update_date")

### **Applying Joins With The Old Records**

In [0]:
df_join = df.join(df_old, df.customer_id == df_old["old_customer_id"], "left")

In [0]:
df_join.display()

customer_id email city state domains full_name old_DimCustomerKey old_customer_id old_create_date old_update_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney null null null null C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers null null null null C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes null null null null C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott null null null null C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez null null null null C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy null null null null C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle null null null null C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos null null null null C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green null null null null C00010 charles58@murillo.net West Hector OK murillo.net James Myers null null null null C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le null null null null C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks null null null null C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin null null null null C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman null null null null C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris null null null null C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker null null null null C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter null null null null C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang null null null null C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King null null null null C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins null null null null C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins null null null null C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn null null null null C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart null null null null C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens null null null null C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett null null null null C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris null null null null C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez null null null null C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker null null null null C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson null null null null C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins null null null null C00031 kramerkaylee@hotmail.com Travisview CT hotmail.com Jeanette Smith null null null null C00032 egallegos@gmail.com Samuelshire KS gmail.com Alexandria Singleton null null null null C00033 lindasummers@hotmail.com South Andrewchester CO hotmail.com Carrie Wheeler null null null null C00034 stacy78@gmail.com Gregorybury IA gmail.com Carol Matthews null null null null C00035 jnorris@gmail.com Angelafurt MD gmail.com Samantha Hernandez null null null null C00036 jesustaylor@hotmail.com Port Nicoleborough AR hotmail.com Jacob Mccoy null null null null C00037 eric78@hotmail.com Millerfurt VT hotmail.com Holly Arnold null null null null C00038 ythomas@hotmail.com Port Michaelstad MS hotmail.com Robert Haas null null null null C00039 angela55@hotmail.com Lake Michaelhaven AL hotmail.com Teresa Ward null null null null C00040 christianrogers@gmail.com New Michael TX gmail.com Francisco Horne null null null null C00041 pbarnes@hotmail.com Allisonhaven AK hotmail.com James Brooks null null null null C00042 hannasteven@yahoo.com South Garrettton IA yahoo.com Jenna Lewis null null null null C00043 ronnie19@hotmail.com South Johnville OK hotmail.

### **Seperating New vs Old Records**

In [0]:
df_new = df_join.filter(df_join['old_DimCustomerKey'].isNull())

In [0]:
df_old = df_join.filter(df_join['old_DimCustomerKey'].isNotNull())

### **Preparing df_old**

In [0]:
# dropping all the columns which are not required

df_old = df_old.drop("old_customer_id", "old_update_date")

# Renaming "old_DimCustomerKey" column to "DimCustomerKey"

df_old = df_old.withColumnRenamed("old_DimCustomerKey", "DimCustomerKey")

# Renaming "old_create_date" column to "create date"

df_old = df_old.withColumnRenamed("old_create_date", "create_date")
df_old = df_old.withColumn("create_date", to_timestamp(col("create_date")))

# Recreating "update_date" column with current timestamp

df_old = df_old.withColumn("update_date", current_timestamp())

In [0]:
df_old.display()

customer_id email city state domains full_name DimCustomerKey create_date update_date

### **Preparing df_new**

In [0]:
# dropping all the columns which are not required

df_new = df_new.drop("old_DimCustomerKey", "old_customer_id", "old_update_date", "old_create_date")

# Recreating "update_date", "current_date" column with current timestamp

df_new = df_new.withColumn("update_date", current_timestamp())
df_new = df_new.withColumn("create_date", current_timestamp())

In [0]:
df_new.display()

customer_id email city state domains full_name update_date create_date C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00010 charles58@murillo.net West Hector OK murillo.net James Myers 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00031 kramerkaylee@hotmail.com Travisview CT hotmail.com Jeanette Smith 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00032 egallegos@gmail.com Samuelshire KS gmail.com Alexandria Singleton 2025-12-23T14:59:37.648Z 2025-12-23T14:59:37.648Z C00033 lindasummers@hotmail.com South Andrewchester 

### **Surrogate Key - From 1**

In [0]:
df_new = df_new.withColumn("DimCustomerKey", monotonically_increasing_id()+lit(1))

In [0]:
df_new.display()

customer_id email city state domains full_name update_date create_date DimCustomerKey C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 1 C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 2 C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 3 C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 4 C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 5 C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 6 C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 7 C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 8 C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 9 C00010 charles58@murillo.net West Hector OK murillo.net James Myers 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 10 C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 11 C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 12 C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 13 C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 14 C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 15 C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 16 C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 17 C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 18 C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 19 C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 20 C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 21 C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 22 C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 23 C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 24 C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 25 C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 26 C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 27 C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 28 C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 29 C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 30 C00031 kramerkaylee@hotmail.com Travisview CT hotmail.com Jeanette Smith 2025-12-23T14:59:38.344Z 2025-12-23T14:59:38.344Z 31 C00032 egallegos@gmail.com Samuelshire KS gmail.com Alexandria Singleton 202

In [0]:
df.limit(10).display()

customer_id email city state domains full_name C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green C00010 charles58@murillo.net West Hector OK murillo.net James Myers

### **Adding Max Surrogate Key**

In [0]:
if init_load_flag ==1:
  max_surrogate_key = 0

else:
  df_maxsur = spark.sql("select max(DimCustomerKey) as max_surrogate_key from databricks_cata.gold.DimCustomers")

  # Converting df_maxsur to max_surrogate_key
  max_surrogate_key = df_maxsur.collect()[0]["max_surrogate_key"]


In [0]:
df_new = df_new.withColumn("DimCustomerKey",lit(max_surrogate_key)+col("DimCustomerKey"))

### **Union of df_old and df_new**

In [0]:
df_final = df_new.unionByName(df_old)

In [0]:
df_final.display()

customer_id email city state domains full_name update_date create_date DimCustomerKey C00001 rushjeff@ryan.org Johnsonmouth MS ryan.org Emily Mooney 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 1 C00002 mccoykiara@kelly.com Stephenfort WY kelly.com Andrea Sellers 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 2 C00003 rebeccamiller@yahoo.com South Stephenshire LA yahoo.com Craig Hayes 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 3 C00004 lawrence05@campbell.info Chrisland ND campbell.info Bryan Scott 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 4 C00005 carrie45@yahoo.com East Dennistown RI yahoo.com Sean Vasquez 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 5 C00006 traceyramos@gmail.com North Matthew IN gmail.com Kevin Mccarthy 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 6 C00007 scottallen@gmail.com Joneshaven VA gmail.com Amanda Doyle 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 7 C00008 sullivanjeremy@horton-adams.com South Nathanfurt CT horton-adams.com Paul Campos 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 8 C00009 dennis03@yahoo.com Kimberlyview MD yahoo.com Mary Green 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 9 C00010 charles58@murillo.net West Hector OK murillo.net James Myers 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 10 C00011 anita65@gmail.com Houstonfurt AR gmail.com Jacob Le 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 11 C00012 beardtravis@gmail.com East Jenniferview WI gmail.com Chad Banks 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 12 C00013 jwood@gmail.com Lake Gregoryshire OR gmail.com James Martin 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 13 C00014 lmoore@yahoo.com East Tiffanybury MS yahoo.com Thomas Hartman 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 14 C00015 daniellowe@hotmail.com South Courtney SC hotmail.com Diane Harris 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 15 C00016 amylam@collins.org Jesusburgh IA collins.org Brett Parker 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 16 C00017 rhondaferguson@gmail.com West Loriborough GA gmail.com Angela Carter 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 17 C00018 martinfrank@brooks.info Lake Joshuamouth OH brooks.info Darrell Chang 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 18 C00019 russelltimothy@simpson-hunter.com East Anthonyland NY simpson-hunter.com Angie King 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 19 C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 20 C00021 morgancraig@stephens.com South Charles ND stephens.com Brian Hawkins 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 21 C00022 pshepherd@walker-kelly.com Harrisland TN walker-kelly.com Jeanne Hahn 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 22 C00023 greg64@banks.com North Kara NM banks.com Jackie Stewart 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 23 C00024 andreawilliams@yahoo.com Stewartport NM yahoo.com Heather Owens 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 24 C00025 dawn65@yahoo.com Port Juliebury IN yahoo.com Christina Bennett 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 25 C00026 rebecca20@yahoo.com Ortizshire WY yahoo.com Mark Harris 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 26 C00027 ashley08@mckinney.info Mosleyburgh NM mckinney.info Brandy Juarez 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 27 C00028 steven27@gmail.com North Gregoryfurt NM gmail.com Barry Baker 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 28 C00029 irandall@camacho-smith.com Kaiserhaven OR camacho-smith.com Michael Johnson 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 29 C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 30 C00031 kramerkaylee@hotmail.com Travisview CT hotmail.com Jeanette Smith 2025-12-23T14:59:39.668Z 2025-12-23T14:59:39.668Z 31 C00032 egallegos@gmail.com Samuelshire KS gmail.com Alexandria Singleton 202

### **SCD Type - 1**

In [0]:
from delta.tables import DeltaTable

In [0]:
if spark.catalog.tableExists("databricks_cata.gold.DimCustomers"):
    dlt_obj = DeltaTable.forPath(spark,"abfss://gold@sriharsan1databricks.dfs.core.windows.net/DimCustomers")
    dlt_obj.alias("trg").merge(df_final.alias("src"),"trg.DimCustomerKey = src.DimCustomerKey")\
        .whenMatchedUpdateAll()\
        .whenNotMatchedInsertAll()\
        .execute()
else:
     df_final.write.mode("overwrite")\
        .format("delta")\
        .option("path","abfss://gold@sriharsan1databricks.dfs.core.windows.net/DimCustomers")\
        .saveAsTable("databricks_cata.gold.DimCustomers")

In [0]:
%sql
select * from databricks_cata.gold.dimcustomers

customer_id email city state domains full_name update_date create_date DimCustomerKey C01220 matthew01@yahoo.com New Andrewhaven WA yahoo.com Thomas Fitzgerald 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 1 C01579 nathancastro@gmail.com South Amanda FL gmail.com Brittany Schmidt 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 2 C01155 cynthia51@lewis-dixon.com East Theresa FL lewis-dixon.com Latasha Phelps 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 3 C01943 rodriguezzachary@hotmail.com East Timothy PA hotmail.com David Cooper 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 4 C01554 sthompson@harding.com New Leefurt ME harding.com Gavin Lindsey 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 5 C00767 rsmith@pruitt-hodges.net Heatherton IL pruitt-hodges.net Pam Watts 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 6 C01097 joel22@stone-holmes.com Davidhaven LA stone-holmes.com James Martinez 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 7 C01674 crystalraymond@keller.com Hoborough ME keller.com Nicole Johnston 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 8 C00215 petersonthomas@yahoo.com South Andrea OK yahoo.com Danielle Huerta 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 9 C00587 phillipsstephanie@gmail.com New Ronaldmouth OR gmail.com Michael Bailey 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 10 C01181 sara80@hotmail.com Howardborough MI hotmail.com Katrina Tran 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 11 C01183 lauragrant@terrell.com Jamesbury MS terrell.com Victor Lara 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 12 C00469 tholland@gmail.com North Darleneport IL gmail.com James Terry 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 13 C01263 lawsonrachel@hotmail.com Blackville NE hotmail.com Mary Morgan 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 14 C01985 allisonmaddox@hotmail.com Summersland GA hotmail.com Richard Martin 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 15 C00182 chelseanorris@brown-freeman.com Davidburgh AL brown-freeman.com Cynthia Hernandez 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 16 C01312 ngarrett@dixon.com Oliviatown DC dixon.com Deborah Gordon 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 17 C01567 heathergaines@edwards-english.com Mcneilchester IA edwards-english.com Ruth Miles 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 18 C00030 cfuller@gmail.com Port Coltonton AL gmail.com Holly Collins 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 19 C01658 scottcox@fisher.org Port Timothyborough FL fisher.org Jessica Salas 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 20 C00758 leonardwilliams@burns.org Osborneburgh VA burns.org Michael Roman 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 21 C01327 stephanie26@berry.com Carolynberg NJ berry.com Sean Brown 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 22 C00688 ehill@george.info Harristown WI george.info Jennifer Burns 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 23 C00828 markhickman@parks.com Mcdanielchester OK parks.com Phillip Marquez 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 24 C01319 thomas26@gmail.com Nathanielton IL gmail.com Abigail Martinez 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 25 C01711 xwilliams@yahoo.com Michaelhaven OH yahoo.com Ian Solis 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 26 C00020 rojassandra@hotmail.com South Oscar NV hotmail.com Juan Collins 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 27 C00176 griffinamanda@yahoo.com New Mary OR yahoo.com Daniel Barnes 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 28 C00494 zwright@hernandez.com Kaylaborough VA hernandez.com Lisa Clayton 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 29 C01692 gpeterson@newman-ellis.com Davidmouth KS newman-ellis.com Kyle Clark 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 30 C00944 joseph55@yahoo.com East Jessicaville NC yahoo.com Linda Gill 2025-12-23T14:59:45.715Z 2025-12-23T14:59:45.715Z 31 C00999 munozlisa@yahoo.com Nort